#### 1. 임포트 - 파이참 터미널에 jupyter nbconvert --to script coffeeStore.ipynb 입력

In [43]:
import pandas as pd
import numpy as np
import folium
import requests

from bs4 import BeautifulSoup

# pip install tqdm : progressBar 구현
from tqdm.notebook import tqdm 
from selenium import webdriver

from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.chrome.service import Service

#### 2. 드라이브 객체 생성

In [44]:
chrome_options = webdriver.ChromeOptions()  # 크롬 브라우저 옵션
drive_path = 'chromedriver.exe'  # 다운로드 받은 드라이버 파일
my_service = Service(drive_path)  # 드라이버 제어를 위한 서비스 객체
driver = webdriver.Chrome(service=my_service, options=chrome_options)  # 드라이버 객체
print(type(driver))  # 객체가 잘 생성되었는지 확인

driver.maximize_window()  # 윈도우 창 최대화

<class 'selenium.webdriver.chrome.webdriver.WebDriver'>


#### 3. 크롤링 환경 설정

In [45]:
wait_time = 10 # 최대 대기 시간
driver.implicitly_wait(wait_time)

#### 4. 스타벅스) 매장 찾기 - 지역 검색 링크 주소

In [46]:
starbucks_url = 'https://www.starbucks.co.kr/store/store_map.do?disp=locale'
driver.get(starbucks_url)  # 해당 페이지로 이동

#### 5. 스타벅스) '서울' 링크 클릭

In [47]:
starbucks_seoul_selector = '#container > div > form > fieldset > div > section > article.find_store_cont > article > article:nth-child(4) > div.loca_step1 > div.loca_step1_cont > ul > li:nth-child(1) > a'
WebDriverWait(driver, 5).until(EC.presence_of_element_located((By.CSS_SELECTOR, starbucks_seoul_selector))).click() # 클릭 텀을 주기

#### 6. 스타벅스) '서울'-' 전체' 클릭

In [48]:
starbucks_seoul_all = '#mCSB_2_container > ul > li:nth-child(1) > a'
WebDriverWait(driver, 5).until(EC.presence_of_element_located((By.CSS_SELECTOR, starbucks_seoul_all))).click()  # 클릭 텀을 주기

In [49]:
# (수업 - 굳이 html 파일로 만드는 이유가 없음. 플젝 시 삭제) 스타벅스 html 코드를 파싱하여 html 파일에 기록
html = driver.page_source  # 해당 페이지의 소스 코드 반환
file_name='starbucks.html'
html_file= open(file_name, 'w', encoding='UTF-8')
print(html, file=html_file)
html_file.close()
print(file_name + '파일 생성됨')

starbucks.html파일 생성됨


In [14]:
# BeautifulSoup사이트 링크: https://www.crummy.com/software/BeautifulSoup/bs4/doc/
# (수업 - 굳이 html 파일로 만드는 이유가 없음. 플젝 시 삭제) 파싱된 결과를 Beautiful Soup 객체로 생성
soup = BeautifulSoup(html, 'html.parser')
print(type(soup))

<class 'bs4.BeautifulSoup'>


#### 7. 스타벅스 html 코드를 받아와 출력하기 - 현지님 코드(짱...)

In [50]:
html = driver.page_source  # 해당 페이지의 소스 코드 반환
soup = BeautifulSoup(html, 'html.parser')
print(soup)

<html lang="ko"><head>
<meta content="IE=edge" http-equiv="X-UA-Compatible"/>
<meta charset="utf-8"/>
<meta content="width=device-width, initial-scale=1.0, maximum-scale=1.0, minimum-scale=1.0, user-scalable=no" name="viewport"/>
<meta content="website" property="og:type"/>
<meta content="Starbucks" property="og:title"/>
<meta content="https://www.starbucks.co.kr/" property="og:url"/>
<meta content="https://image.istarbucks.co.kr/common/img/kakaotalk.png" property="og:image"/>
<meta content="Starbucks" property="og:description"/>
<title id="titleJoin">Starbucks Korea</title><script async="" src="https://www.googletagmanager.com/gtag/js?id=G-WC8Q3C59QP&amp;cx=c&amp;_slc=1" type="text/javascript"></script><script async="" crossorigin="anonymous" src="https://connect.facebook.net/ko_KR/sdk.js?hash=e0968414a5151d56439e06a3b0de7a93"></script><script id="facebook-jssdk" src="//connect.facebook.net/ko_KR/sdk.js"></script><script async="" src="//www.google-analytics.com/analytics.js"></script>

#### 8. 매장 정보를 담고 있는 컨테이너 박스를 찾기

In [51]:
# 컨테이너는 div 태그이고, id는 mCSB_3_container
container = soup.find('div', id='mCSB_3_container')
starbucks_store_all = container.find_all('li')
print('store_all : ', len(starbucks_store_all))

store_all :  615


#### 9. 매장 정보에서 필요한 데이터를 리스트로 추출

In [52]:
starbucks_data = []

for store in starbucks_store_all:
    # print(store)
    brand = '스타벅스'
    name = store.find('strong').text.strip()  # 가게 한 군데 정보를 가진 store 에서 strong 을 찾아서 공백 제거한 텍스트로 출력해라
    address = store.find('p', 'result_details').get_text(separator='\n').split('\n')[0].strip()
    address_data = address.split(' ')
    dddress_city = address_data[0]
    address_gu = address_data[1]
    latitude = store['data-lat']  # 위도
    ongitude = store['data-long']  # 경도

    print('[' + name + ']')
    print('[주소:', address, ']')
    
    starbucks_data.append([brand, name, address, dddress_city, address_gu, latitude, ongitude])
    
    # break

print(len(starbucks_data))

[역삼아레나빌딩]
[주소: 서울특별시 강남구 언주로 425 (역삼동) ]
[논현역사거리]
[주소: 서울특별시 강남구 강남대로 538 (논현동) ]
[신사역성일빌딩]
[주소: 서울특별시 강남구 강남대로 584 (논현동) ]
[국기원사거리]
[주소: 서울특별시 강남구 테헤란로 125 (역삼동) ]
[대치재경빌딩]
[주소: 서울특별시 강남구 남부순환로 2947 (대치동) ]
[봉은사역]
[주소: 서울특별시 강남구 봉은사로 619 (삼성동) ]
[압구정윤성빌딩]
[주소: 서울특별시 강남구 논현로 834 (신사동) ]
[코엑스별마당]
[주소: 서울특별시 강남구 영동대로 513 (삼성동) ]
[삼성역섬유센터R]
[주소: 서울특별시 강남구 테헤란로 518 (대치동) ]
[압구정R]
[주소: 서울특별시 강남구 언주로 861 (신사동) ]
[수서역R]
[주소: 서울특별시 강남구 광평로 281 (수서동) ]
[양재강남빌딩R]
[주소: 서울특별시 강남구 남부순환로 2621 (도곡동) ]
[선릉동신빌딩R]
[주소: 서울특별시 강남구 테헤란로 409 (삼성동) ]
[봉은사로선정릉]
[주소: 서울특별시 강남구 봉은사로 446 (삼성동) ]
[강남오거리]
[주소: 서울특별시 강남구 봉은사로2길 39 (역삼동) ]
[스타필드코엑스몰R]
[주소: 서울특별시 강남구 영동대로 513 (삼성동) 코엑스 A106호 ]
[강남구청정문]
[주소: 서울특별시 강남구 학동로 419 (청담동) ]
[도곡공원]
[주소: 서울특별시 강남구 도곡로 205 (역삼동) ]
[강남R]
[주소: 서울특별시 강남구 강남대로 390 (역삼동) ]
[대치은마사거리]
[주소: 서울특별시 강남구 도곡로 457 (대치동) ]
[청담영동대로]
[주소: 서울특별시 강남구 영동대로 720 (청담동) ]
[압구정]
[주소: 서울특별시 강남구 압구정로30길 17 (신사동) ]
[신사가로수]
[주소: 서울특별시 강남구 가로수길 59 ]
[청담스타R]
[주소: 서울특별시 강남구 도산대로57길 24 (청담동) ]
[강남우성]
[주소: 서울특별

#### 10. pandas 데이터프레임에 9번의 매장 정보를 담은 리스트(starbucks_data) 할당 / 칼럼명 정하기 / 앞 7개 항목만 출력하기 

In [53]:
starbucks_df = pd.DataFrame(starbucks_data)
starbucks_df.columns = ['브랜드', '상호', '주소', '도시','군구', '위도', '경도']
starbucks_df.head(n=7)
# starbucks_df.tail(n=7)

브랜드       상호                          주소     도시   군구          위도  \
0  스타벅스  역삼아레나빌딩     서울특별시 강남구 언주로 425 (역삼동)  서울특별시  강남구   37.501087   
1  스타벅스   논현역사거리    서울특별시 강남구 강남대로 538 (논현동)  서울특별시  강남구   37.510178   
2  스타벅스  신사역성일빌딩    서울특별시 강남구 강남대로 584 (논현동)  서울특별시  강남구  37.5139309   
3  스타벅스   국기원사거리    서울특별시 강남구 테헤란로 125 (역삼동)  서울특별시  강남구   37.499517   
4  스타벅스   대치재경빌딩  서울특별시 강남구 남부순환로 2947 (대치동)  서울특별시  강남구   37.494668   
5  스타벅스     봉은사역    서울특별시 강남구 봉은사로 619 (삼성동)  서울특별시  강남구   37.515000   
6  스타벅스  압구정윤성빌딩     서울특별시 강남구 논현로 834 (신사동)  서울특별시  강남구  37.5227934   

            경도  
0   127.043069  
1   127.022223  
2  127.0206057  
3   127.031495  
4   127.062583  
5   127.063196  
6  127.0286009

#### 11. 위도/경도 누락 건 확인

In [54]:
print('위도 누락 데이터 개수: ', starbucks_df['위도'].isnull().sum())
print('경도 누락 데이터 개수: ', starbucks_df['경도'].isnull().sum())

위도 누락 데이터 개수:  0
경도 누락 데이터 개수:  0


#### 12. 구 목록 추출하기

In [55]:
gu_list = list(starbucks_df['군구'].unique())
print('서울시 구 목록 개수:', len(gu_list))
print(gu_list)

서울시 구 목록 개수: 25
['강남구', '강북구', '강서구', '관악구', '광진구', '금천구', '노원구', '도봉구', '동작구', '마포구', '서대문구', '서초구', '성북구', '송파구', '양천구', '영등포구', '은평구', '종로구', '중구', '강동구', '구로구', '동대문구', '성동구', '용산구', '중랑구']


#### 4. 이디야) 매장 찾기 - 지역 검색 링크 주소

In [29]:
ediya_url = 'https://ediya.com/contents/find_store.html'
driver.get(ediya_url)

#### 5. 이디야) '매장명'과 '주소' 검색에서 '주소' 클릭

In [30]:
ediya_address_selector = '#contentWrap > div.contents > div > div.store_search_pop > ul > li:nth-child(2) > a'
WebDriverWait(driver, 5).until(EC.presence_of_element_located((By.CSS_SELECTOR, ediya_address_selector))).click() # 클릭 텀을 주기

#### 6. kakao develope 의 API 서버가 요청 권한을 확인하는 데에 사용됨 

###### 누락된 위도와 경도 정보는 kakao api를 이용하여 채워 넣기
###### https://developers.kakao.com/
###### kakao에 로그인하여 AIP 키 발급 받기

In [31]:
url_header = 'https://dapi.kakao.com/v2/local/search/address.json?query='
api_key = '0269a87bb7a51e49428968569eb95275'
header = {'Authorization': 'KakaoAK ' + api_key}

#### 7. '주소'를 입력 받아서 위도와 경도를 반환해주는 함수 구현

In [32]:
def getGeoCoder(address):
    result = ""
    url = url_header + address
    response = requests.get(url, headers=header)
    # print(response) # 성공시 <Response [200]>으로 리턴 됨
    # print(response.json())
    if response.status_code == 200:
        try:
            result_address = response.json()["documents"][0]["address"]
            result = result_address["y"], result_address["x"]
        except Exception as err:
            return None
    else:
        result = "ERROR[" + str(response.status_code) + "]"

    return result
# end def

#### 한 개의 매장에 대한 테스트를 진행합니다.

In [70]:
geo_info = getGeoCoder('서울 중랑구 망우로 460 (망우동)') # 잘 동작하는 주소
# geo_info = getGeoCoder('서울 노원구 한글비석로 409 (상계동) 1~2층') # NoneType이 리턴되는 주소
geo_info

{'documents': [{'address': {'address_name': '서울 중랑구 망우동 202-9', 'b_code': '1126010500', 'h_code': '1126065500', 'main_address_no': '202', 'mountain_yn': 'N', 'region_1depth_name': '서울', 'region_2depth_name': '중랑구', 'region_3depth_h_name': '망우본동', 'region_3depth_name': '망우동', 'sub_address_no': '9', 'x': '127.103136691889', 'y': '37.6001065609187'}, 'address_name': '서울 중랑구 망우로 460', 'address_type': 'ROAD_ADDR', 'road_address': {'address_name': '서울 중랑구 망우로 460', 'building_name': '한성빌딩', 'main_building_no': '460', 'region_1depth_name': '서울', 'region_2depth_name': '중랑구', 'region_3depth_name': '망우동', 'road_name': '망우로', 'sub_building_no': '', 'underground_yn': 'N', 'x': '127.103136691889', 'y': '37.6001065609187', 'zone_no': '02177'}, 'x': '127.103136691889', 'y': '37.6001065609187'}], 'meta': {'is_end': True, 'pageable_count': 1, 'total_count': 1}}


('37.6001065609187', '127.103136691889')

#### 8. 주소를 초기화하고, 입력 받아 검색버튼을 클릭

#### 이디야 html 코드를 받아와 출력하기 - 현지님 코드(짱...)

In [ ]:
ediya_data = []

for gu in tqdm(gu_list):
    ediya_search_keyword_css = '#keyword'
    
    # 이디야 주소 검색어 초기화
    WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.CSS_SELECTOR, ediya_search_keyword_css))).clear()
    
    # 이디야 주소 검색어 입력
    # f"서울 {gu}" : f-string 기법, 서울 중구, 서울 마포구 등등
    WebDriverWait(driver, 10).until(EC.presence_of_element_located
                                    ((By.CSS_SELECTOR, ediya_search_keyword_css))).send_keys(f"서울 {gu}")

    # 이디야 주소 검색 버튼 클릭
    ediya_search_button_css = '#keyword_div > form > button'
    WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.CSS_SELECTOR, ediya_search_button_css))).click()

    html = driver.page_source  # 해당 페이지의 소스 코드 반환
    soup = BeautifulSoup(html, 'html.parser')
    ul_tag = soup.find('ul', id='placesList')

    gu_ediya_list = ul_tag.find_all('li')

    for store in gu_ediya_list:
        brand = '이디야'
        name = store.find('dt').text.strip()
        only_address = store.find('dd').text.strip()
        #dd_tag = store.find('dd')
        #if dd_tag:
        #    only_address = dd_tag.get_text(strip=True)
        address_data = only_address.split(' ')
        city = address_data[0]
        gu = address_data[1]
    
        geo_info_string = store.find('a')['onclick']
        _geo_info_string = geo_info_string  # 중간에 변형이 이루어지므로 임시
    
        latitude = np.nan  # 위도
        longitude = np.nan  # 경도
        latLong = ['0', '0']  # 위도와 경도를 문자열로 저장하는데에 사용
    
        if geo_info_string.startswith("panLatTo"): 
            # 올바른 위도/경도가 아님
            try:
                if geo_info_string.index(r"panLatTo('0','0'") == 0: 
                    geo_info = getGeoCoder(only_address) 
                    if geo_info != None:
                        latitude = geo_info[0] # 위도
                        longitude = geo_info[1] # 경도
                    else:
                        print(address)
                    #end if
                 # end if
            except ValueError as err:
                # 올바른 위도/경도입니다.
                latLong = geo_info_string.replace(r"panLatTo('", '').replace(r"');fnMove();", '')
                latLong = latLong.split("','")
                latitude = latLong[1] 
                longitude = latLong[0]    
            # end try
    
            # 'panAddTo'으로 시작하는 경우
        else: 
            geo_info = getGeoCoder(only_address) 
            if geo_info != None:
                latitude = geo_info[0] # 위도
                longitude = geo_info[1] # 경도
            else:
                print(only_address)
            # end if
    
            # 올바른 위도 경도 형식이 아니면
            if latLong[1] == '0' or latLong[0] == '0':            
                # 카카오 지도 api 이용하여 위도와 경도를 취득합니다.
                geo_info = getGeoCoder(only_address) 
                if geo_info != None:
                    latitude = geo_info[0] # 위도
                    longitude = geo_info[1] # 경도
                else:
                    print(only_address)
            # end if
            
        ediya_data.append([brand, name, only_address, gu, latitude, longitude]) 
        print('-'*30)
        print(ediya_data)
    
    

  0%|          | 0/25 [00:00<?, ?it/s]

------------------------------
[['이디야', '강남YMCA점', '서울 강남구 논현동', '중랑구', '37.5126451506882', '127.030154778539']]
------------------------------
[['이디야', '강남YMCA점', '서울 강남구 논현동', '중랑구', '37.5126451506882', '127.030154778539'], ['이디야', '강남구청역아이티웨딩점', '서울 강남구 학동로 338 (논현동, 강남파라곤)', '중랑구', '37.51654171724045', '127.0401601992311']]
------------------------------
[['이디야', '강남YMCA점', '서울 강남구 논현동', '중랑구', '37.5126451506882', '127.030154778539'], ['이디야', '강남구청역아이티웨딩점', '서울 강남구 학동로 338 (논현동, 강남파라곤)', '중랑구', '37.51654171724045', '127.0401601992311'], ['이디야', '강남논현학동점', '서울 강남구 논현로131길 28 (논현동)', '중랑구', '37.51408005446769', '127.02810578707652']]
------------------------------
[['이디야', '강남YMCA점', '서울 강남구 논현동', '중랑구', '37.5126451506882', '127.030154778539'], ['이디야', '강남구청역아이티웨딩점', '서울 강남구 학동로 338 (논현동, 강남파라곤)', '중랑구', '37.51654171724045', '127.0401601992311'], ['이디야', '강남논현학동점', '서울 강남구 논현로131길 28 (논현동)', '중랑구', '37.51408005446769', '127.02810578707652'], ['이디야', '강남대치점', '서울 강남구 역삼로 415 (대치동, 성진빌

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



------------------------------
[['이디야', '강남YMCA점', '서울 강남구 논현동', '중랑구', '37.5126451506882', '127.030154778539'], ['이디야', '강남구청역아이티웨딩점', '서울 강남구 학동로 338 (논현동, 강남파라곤)', '중랑구', '37.51654171724045', '127.0401601992311'], ['이디야', '강남논현학동점', '서울 강남구 논현로131길 28 (논현동)', '중랑구', '37.51408005446769', '127.02810578707652'], ['이디야', '강남대치점', '서울 강남구 역삼로 415 (대치동, 성진빌딩)', '중랑구', '37.50133876179308', '127.05242928262568'], ['이디야', '강남도산점', '서울 강남구 도산대로37길 20 (신사동)', '중랑구', '37.5222784215718', '127.031487626912'], ['이디야', '강남율현점', '서울 강남구 밤고개로21길 8 (율현동, 세곡프라자)', '중랑구', '37.4735487656314', '127.107863694133'], ['이디야', '개포동역점', '서울 강남구 개포로82길 11 (개포동, 삼우빌딩)', '중랑구', '37.488604436046536', '127.06742226515867'], ['이디야', '건설회관점', '서울 강남구 언주로 711 (논현동)', '중랑구', '37.5170777485054', '127.033430008152'], ['이디야', '대청역점', '서울 강남구 개포로109길 34 (개포동, 대청프라자)', '중랑구', '37.49418891219431', '127.07764131137398'], ['이디야', '대치역점', '서울 강남구 남부순환로 2937 (대치동, 까치빌딩)', '중랑구', '37.4940924880388', '127.061617564506'], ['이디야', '도

##### 위의 코드에서 메서드로 뽑아내기 위해서... 

In [59]:
def is_true_
if geo_info_string.startswith("panLatTo"): 
            # 올바른 위도/경도가 아님
            try:
                if geo_info_string.index(r"panLatTo('0','0'") == 0: 
                    geo_info = getGeoCoder(only_address) 
                    if geo_info != None:
                        latitude = geo_info[0] # 위도
                        longitude = geo_info[1] # 경도
                    else:
                        print(address)
                    #end if
                 # end if
            except ValueError as err:
                # 올바른 위도/경도입니다.
                latLong = geo_info_string.replace(r"panLatTo('", '').replace(r"');fnMove();", '')
                latLong = latLong.split("','")
                latitude = latLong[1] 
                longitude = latLong[0]    
            # end try
    
            # 'panAddTo'으로 시작하는 경우
        else: 
            geo_info = getGeoCoder(only_address) 
            if geo_info != None:
                latitude = geo_info[0] # 위도
                longitude = geo_info[1] # 경도
            else:
                print(only_address)
            # end if
    
            # 올바른 위도 경도 형식이 아니면
            if latLong[1] == '0' or latLong[0] == '0':            
                # 카카오 지도 api 이용하여 위도와 경도를 취득합니다.
                geo_info = getGeoCoder(only_address) 
                if geo_info != None:
                    latitude = geo_info[0] # 위도
                    longitude = geo_info[1] # 경도
                else:
                    print(only_address)
            # end if

IndentationError: unindent does not match any outer indentation level (<string>, line 22)

In [41]:
ediya_df = pd.DataFrame(ediya_data)
ediya_df.columns = ['브랜드', '상호', '주소', '도시', '군구', '위도', '경도']
ediya_df

브랜드      상호                                       주소  도시   군구  \
0    이디야   금란망우점                     서울 중랑구 망우로 460 (망우동)  서울  중랑구   
1    이디야  동원사거리점             서울 중랑구 겸재로 240 (면목동, 행복오피스텔)  서울  중랑구   
2    이디야    망우동점                     서울 중랑구 망우로 416 (망우동)  서울  중랑구   
3    이디야   망우중앙점  서울 중랑구 용마산로115길 109 (망우동, 한일써너스빌리젠시2단지)  서울  중랑구   
4    이디야  망우코레일점           서울 중랑구 망우로55길 11-10 (상봉동, 망우역)  서울  중랑구   
..   ...     ...                                      ...  ..  ...   
568  이디야     용문점                 서울 용산구 원효로41길 73 (원효로2가)  서울  용산구   
569  이디야   용산원효점              서울 용산구 원효로 70 (원효로4가, 신정빌딩)  서울  용산구   
570  이디야   용산청파점          서울 용산구 청파로71길 10 (청파동1가, 새마을금고)  서울  용산구   
571  이디야   용산효창점                   서울 용산구 효창원로66길 2 (효창동)  서울  용산구   
572  이디야    원효로점                   서울 용산구 원효로 257 (원효로1가)  서울  용산구   

                     위도                  경도  
0      37.6001065609187    127.103136691889  
1      37.5896269575279    127.094182772191  
2      37.5991657770242    127.098351137589  
3      37.5974674047065  127.09415879594557  
4      37.5992876153903    127.092756577852  
..                  ...                 ...  
568   37.53584882357322   126.9611373908156  
569    37.5325054872953    126.951642152118  
570    37.5494639189725    126.969413497587  
571  37.540537976136086  126.96220762686157  
572    37.5405688166185    126.969114679317  

[573 rows x 7 columns]

In [36]:
print('위도 누락 데이터 개수: ', ediya_df['위도'].isnull().sum())
print('경도 누락 데이터 개수: ', ediya_df['경도'].isnull().sum())

위도 누락 데이터 개수:  4
경도 누락 데이터 개수:  4


In [56]:
print('스타벅스 매장 개수:', len(starbucks_df))
print('이디야 매장 개수:', len(ediya_df))

스타벅스 매장 개수: 615
이디야 매장 개수: 573


#### 스타벅스와 이디야 매장의 데이터 프레임을 합치기

In [131]:
# ediya_df = ediya_df.drop('geo_info_Imsi', axis=1)  # 임시 컬럼 제거하는 코드. 임시컬럼 설정을 안 해서 형식만 알아두면 좋을듯
store_frame = pd.concat([ediya_df, starbucks_df])
print('전체 매장 개수: ', len(store_frame))
store_frame['도시'].unique()

전체 매장 개수:  1188


array(['서울', '서울특별시'], dtype=object)

#### 보정을 위한 텍스트 파일을 읽어서, 사전 생성

In [132]:
change_city_name_txt = open('change_city_name.txt', mode='rt', encoding='UTF-8')
city_name_dict=dict()

city_names = change_city_name_txt.readlines()
print(type(city_names))

for name in city_names:
    my_data = name.replace('\n', '').split(':')
    city_name_dict[my_data[0]] = my_data[1]

print(city_name_dict)

<class 'list'>
{'서울': '서울특별시', '서울시': '서울특별시', '진해': '창원', '마산': '창원', '부산': '부산광역시', '부산시': '부산광역시'}


In [133]:
store_frame.loc[:, '도시'] = store_frame.loc[:, '도시'].apply(lambda city : city_name_dict.get(city, city))
store_frame['도시'].unique()

array(['서울특별시'], dtype=object)

#### 위도에 누락된 매장 정보 확인

In [137]:
missing_latitude = store_frame[store_frame['위도'].isnull()]
missing_latitude

Empty DataFrame
Columns: [브랜드, 상호, 주소, 도시, 군구, 위도, 경도]
Index: []

#### (수업 - 쓸데없는 코드, 지우기) 위도 경도를 수동으로 넣어 주기 - > 자동으로 넣어주어야 함

In [135]:
store_frame.loc[170, ['위도', '경도']] = [37.5, 127.05]
store_frame.loc[219, ['위도', '경도']] = [37.5, 127.05]
store_frame.loc[223, ['위도', '경도']] = [37.5, 127.05]
store_frame.loc[388, ['위도', '경도']] = [37.5, 127.05]

#### 위도 누락된 매장 정보에 수동 경로 들어갔는지 확인 

In [136]:
missing_latitude = store_frame[store_frame['위도'].isnull()]
missing_latitude

Empty DataFrame
Columns: [브랜드, 상호, 주소, 도시, 군구, 위도, 경도]
Index: []

#### 파일로 저장하기

In [86]:
file_name = 'store_list.csv'
# store_frame.to_csv(file_name, encoding='CP949', index=False)  # 엑셀에서 보는 방법
store_frame.to_csv(file_name, encoding='UTF-8', index=False)  # 일반적인 방법
print(file_name + '파일 저장됨')

store_list.csv파일 저장됨


#### 지도 그리기: '군구' 컬럼이 '마포구', '용산구', '서대문구' 인 항목들만 추출

In [138]:
select_gu_frame = store_frame[store_frame['군구'].isin(['마포구', '용산구', '서대문구'])]
print(len(select_gu_frame), '개')

138 개


In [141]:
select_gu_frame['위도'] = pd.to_numeric(select_gu_frame['위도'], errors='coerce')
select_gu_frame['경도'] = pd.to_numeric(select_gu_frame['경도'], errors='coerce')

# select_gu_frame.loc[:,'위도'] = pd.to_numeric(select_gu_frame['위도'], errors='coerce')
# select_gu_frame.loc[:,'경도'] = pd.to_numeric(select_gu_frame['경도'], errors='coerce')

select_gu_frame.info()
select_gu_frame['위도'].unique()

<class 'pandas.core.frame.DataFrame'>
Index: 138 entries, 222 to 606
Data columns (total 7 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   브랜드     138 non-null    object 
 1   상호      138 non-null    object 
 2   주소      138 non-null    object 
 3   도시      138 non-null    object 
 4   군구      138 non-null    object 
 5   위도      138 non-null    float64
 6   경도      138 non-null    float64
dtypes: float64(2), object(5)
memory usage: 8.6+ KB


C:\Users\ict-01\AppData\Local\Temp\ipykernel_12148\3086968446.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  select_gu_frame['위도'] = pd.to_numeric(select_gu_frame['위도'], errors='coerce')
C:\Users\ict-01\AppData\Local\Temp\ipykernel_12148\3086968446.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  select_gu_frame['경도'] = pd.to_numeric(select_gu_frame['경도'], errors='coerce')


array([37.54511882, 37.5       , 37.54203652, 37.56479956, 37.56922052,
       37.53980782, 37.55431356, 37.55637639, 37.56079667, 37.54824721,
       37.57942834, 37.57571848, 37.56828845, 37.55636572, 37.56482585,
       37.56030738, 37.55583525, 37.55451671, 37.55031487, 37.5560665 ,
       37.55250069, 37.53998479, 37.54959467, 37.54823534, 37.54825826,
       37.5515008 , 37.55561117, 37.55376198, 37.57440199, 37.57936446,
       37.58457145, 37.58345589, 37.57824224, 37.56678216, 37.5589761 ,
       37.55651118, 37.55766549, 37.56236858, 37.55886101, 37.56367404,
       37.56204444, 37.56128805, 37.57638144, 37.56102262, 37.59457019,
       37.5349441 , 37.52055367, 37.55335289, 37.53144725, 37.54405811,
       37.53309521, 37.53584882, 37.53250549, 37.54946392, 37.54053798,
       37.54056882, 37.551073  , 37.57931427, 37.541186  , 37.554636  ,
       37.5508    , 37.545913  , 37.5509    , 37.557491  , 37.543876  ,
       37.549377  , 37.54997888, 37.548178  , 37.553376  , 37.58

#### (수업 - 위도<를 가지고 뜬금없이 웬 수식...) 다양한 수식 함수

In [147]:
latitude = select_gu_frame['위도']
print(type(latitude))
print('총합: %s' % str(latitude.sum()))
print('최소: %s' % str(latitude.min()))
print('최대: %s' % str(latitude.max()))
print('평균: %s' % str(latitude.mean()))
print('중앙값: %s' % str(latitude.median()))
print('표준 편차: %s' % str(latitude.std()))

<class 'pandas.core.series.Series'>
총합: 5182.291040841952
최소: 37.5
최대: 37.594570187466
평균: 37.55283362928951
중앙값: 37.55423527802193
표준 편차: 0.016978046271204115


#### 지도 가져오기

In [162]:
center_select_gu_frame = [select_gu_frame['위도'].mean(), select_gu_frame['경도'].mean()]
print(center_select_gu_frame)
map_data = folium.Map(location=center_select_gu_frame, zoom_start=14.5, control_scale=True, title='openstreepmap')

[np.float64(37.55283362928951), np.float64(126.94369741275432)]


#### 지도에 스타벅스/이디야 위치 정보에 따라 마커 찍기

In [168]:
for idx, row in select_gu_frame.iterrows():
    if row['브랜드'] == '이디야':
        mk_color = 'darkblue'  # 이디야 마커 색상
        ic_color = 'white'  # 이디야 아이콘 색상
    elif row['브랜드'] == '스타벅스': 
        mk_color = 'green'  # 스타벅스 마커 색상
        ic_color = 'white'  # 스타벅스 아이콘 색상
    else:
        mk_color = 'gray'  # 기본 마커 색상
        ic_color = 'white'  # 기본 아이콘 색상
    # end if

    # 지도에 마커 생성
    folium.Marker(
        location=[row['위도'], row['경도']],
        popup = row['주소'],
        tooltip = row['브랜드'],  # 마커에 마우스를 가져다 대면 툴팁으로 표시됨
        icon = folium.Icon(
            color = mk_color,
            icon_color = ic_color,
            icon = 'coffee',
            prefix='fa'
        )
    ).add_to(map_data)
# end for
map_data

In [ ]:
# 8/9 할일
# 시도 컬럼 추가 / 데이터 표준화(전처리)
# 포리움으로 지도 저장
# 위경도 공란 데이터 Google Maps Geocoding API에서 구해서 수동 구현